In [1]:
import numpy as np
import pandas as pd

import os
import string
from string import digits
import re

from sklearn.utils import shuffle
from sklearn.model_selection import train_test_split
from keras.layers import Input, LSTM, Embedding, Dense, RepeatVector
from keras.models import Model
from keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras import Sequential

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

In [2]:
lines=pd.read_csv("/content/drive/MyDrive/AI-2022 Ru 21st-May'24 11-1AM R BY/NLP resources/Hindi_English_Truncated_Corpus.csv",encoding='utf-8')
lines.head()

source                                   english_sentence                                     hindi_sentence
0        ted  politicians do not have permission to do what ...  राजनीतिज्ञों के पास जो कार्य करना चाहिए, वह कर...
1        ted         I'd like to tell you about one such child,  मई आपको ऐसे ही एक बच्चे के बारे में बताना चाहू...
2  indic2012  This percentage is even greater than the perce...   यह प्रतिशत भारत में हिन्दुओं प्रतिशत से अधिक है।
3        ted  what we really mean is that they're bad at not...     हम ये नहीं कहना चाहते कि वो ध्यान नहीं दे पाते
4  indic2012  .The ending portion of these Vedas is called U...        इन्हीं वेदों का अंतिम भाग उपनिषद कहलाता है।

In [3]:
lines.shape

(127607, 3)

In [4]:
lines['source'].value_counts()

source
tides        50000
ted          39881
indic2012    37726
Name: count, dtype: int64

In [5]:
lines=lines[lines['source']=='ted']

In [6]:
lines.shape

(39881, 3)

In [7]:
lines.head(20)

source                                   english_sentence                                     hindi_sentence
0     ted  politicians do not have permission to do what ...  राजनीतिज्ञों के पास जो कार्य करना चाहिए, वह कर...
1     ted         I'd like to tell you about one such child,  मई आपको ऐसे ही एक बच्चे के बारे में बताना चाहू...
3     ted  what we really mean is that they're bad at not...     हम ये नहीं कहना चाहते कि वो ध्यान नहीं दे पाते
7     ted   And who are we to say, even, that they are wrong   और हम होते कौन हैं यह कहने भी वाले कि वे गलत हैं
13    ted                   So there is some sort of justice                                   तो वहाँ न्याय है
23    ted                                This changed slowly                               धीरे धीरे ये सब बदला
26    ted                               were being produced.                           उत्पन्न नहीं कि जाती थी.
30    ted        And you can see, this LED is going to glow.       और जैसा आप देख रहे है, ये एल.ई.डी. जल उठेगी।
32    ted  to turn on the lights or to bring him a glass ...    लाईट जलाने के लिए या उनके लिए पानी लाने के लिए,
35    ted                       Can you imagine saying that?                       क्या आप ये कल्पना कर सकते है
37    ted  Three: this is a good road in - right near whe...  तीसरी: ये हमारी फ़ैक्ट्री के पास की एक अपेक्षा...
39    ted                                  What's going on?”                                क्या हो रहा है ये?”
42    ted   There are also financial reforms in rural China.          ग्रामीण चीन में आर्थिक नवीनीकरण हुये हैं।
49    ted  the family planning started in Vietnam and the...  वियतनाम में परिवार योजना शुरू हो गई और उनके पर...
51    ted                    I mean, at that time, trust me,                      मेरा मतलब, उस समय, सही मानिए,
53    ted                                     Not only that,                                       बस वही नहीं,
55    ted  humans destroyed the commons that they depende...  मानवों ने उन ही साझे संसाधनों को नष्ट किया जिन...
56    ted  Almost goes to E, but otherwise the play would...  रचना करीब करीब ई तक जाती है, मगर तब तो नाटक ख़...
63    ted  So I want to share with you a couple key insights      मैं आपके साथ कुछ मुख्य सूत्र बाँटना चाहता हूँ
66    ted  Many countries in the [unclear], they need leg...  [अस्पष्ट] के बहुत सारे राष्ट्रों को मान्यता चा...

In [8]:
lines.isna().sum()

source              0
english_sentence    0
hindi_sentence      0
dtype: int64

In [9]:
lines.duplicated().sum()

1078

In [10]:
lines.drop_duplicates(inplace=True)
lines.shape

(38803, 3)

* ### Let us pick any 25000 rows from the dataset.

In [11]:
lines=lines.sample(n=25000,random_state=42)
lines.shape

(25000, 3)

### Preprocessing

In [12]:
# Lowercase all characters
lines['english_sentence']=lines['english_sentence'].apply(lambda x: x.lower())
lines['hindi_sentence']=lines['hindi_sentence'].apply(lambda x: x.lower())

In [13]:
# Remove quotes
lines['english_sentence']=lines['english_sentence'].apply(lambda x: re.sub("'", '', x))
lines['hindi_sentence']=lines['hindi_sentence'].apply(lambda x: re.sub("'", '', x))

In [14]:
exclude = set(string.punctuation) # Set of all special characters
# Remove all the special characters
lines['english_sentence']=lines['english_sentence'].apply(lambda x: ''.join(ch for ch in x if ch not in exclude))
lines['hindi_sentence']=lines['hindi_sentence'].apply(lambda x: ''.join(ch for ch in x if ch not in exclude))

In [15]:
# Remove all numbers from text
remove_digits = str.maketrans('', '', digits)
lines['english_sentence']=lines['english_sentence'].apply(lambda x: x.translate(remove_digits))
lines['hindi_sentence']=lines['hindi_sentence'].apply(lambda x: x.translate(remove_digits))

lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: re.sub("[२३०८१५७९४६]", "", x))


In [16]:
# Remove extra spaces
lines['english_sentence']=lines['english_sentence'].apply(lambda x: x.strip())
lines['hindi_sentence']=lines['hindi_sentence'].apply(lambda x: x.strip())
lines['english_sentence']=lines['english_sentence'].apply(lambda x: re.sub(" +", " ", x))
lines['hindi_sentence']=lines['hindi_sentence'].apply(lambda x: re.sub(" +", " ", x))

In [17]:
lines.head()

source                                   english_sentence                                     hindi_sentence
82040     ted  we still dont know who her parents are who she is  हम अभी तक नहीं जानते हैं कि उसके मातापिता कौन ...
85038     ted                                        no keyboard                                  कोई कुंजीपटल नहीं
58018     ted                    but as far as being a performer                        लेकिन एक कलाकार होने के साथ
74470     ted                        and this particular balloon                                 और यह खास गुब्बारा
122330    ted  and its not as hard as you think integrate cli...  और जितना आपको लगता है यह उतना कठिन नहीं हैअपने...

In [18]:
lines['length_eng_sentence']=lines['english_sentence'].apply(lambda x:len(x.split(" ")))
lines['length_hin_sentence']=lines['hindi_sentence'].apply(lambda x:len(x.split(" ")))

In [19]:
lines.head()

source                                   english_sentence                                     hindi_sentence  length_eng_sentence  length_hin_sentence
82040     ted  we still dont know who her parents are who she is  हम अभी तक नहीं जानते हैं कि उसके मातापिता कौन ...                   11                   14
85038     ted                                        no keyboard                                  कोई कुंजीपटल नहीं                    2                    3
58018     ted                    but as far as being a performer                        लेकिन एक कलाकार होने के साथ                    7                    6
74470     ted                        and this particular balloon                                 और यह खास गुब्बारा                    4                    4
122330    ted  and its not as hard as you think integrate cli...  और जितना आपको लगता है यह उतना कठिन नहीं हैअपने...                   16                   18

In [20]:
lines=lines[lines['length_eng_sentence']<=20]
lines=lines[lines['length_hin_sentence']<=20]

In [21]:
lines.shape

(24916, 5)

In [22]:
print("maximum length of Hindi Sentence ",max(lines['length_hin_sentence']))
print("maximum length of English Sentence ",max(lines['length_eng_sentence']))

maximum length of Hindi Sentence  20
maximum length of English Sentence  20


In [23]:
lines.head()

source                                   english_sentence                                     hindi_sentence  length_eng_sentence  length_hin_sentence
82040     ted  we still dont know who her parents are who she is  हम अभी तक नहीं जानते हैं कि उसके मातापिता कौन ...                   11                   14
85038     ted                                        no keyboard                                  कोई कुंजीपटल नहीं                    2                    3
58018     ted                    but as far as being a performer                        लेकिन एक कलाकार होने के साथ                    7                    6
74470     ted                        and this particular balloon                                 और यह खास गुब्बारा                    4                    4
122330    ted  and its not as hard as you think integrate cli...  और जितना आपको लगता है यह उतना कठिन नहीं हैअपने...                   16                   18

In [24]:
# Tokenization and padding
def tokenize_and_pad(lines, column, max_length):
    tokenizer = Tokenizer()
    tokenizer.fit_on_texts(lines[column])
    sequences = tokenizer.texts_to_sequences(lines[column])
    padded_sequences = pad_sequences(sequences, maxlen=max_length, padding='post')
    return tokenizer, padded_sequences

In [25]:
max_length_src = 20
max_length_tar = 20

In [26]:
eng_tokenizer, eng_sequences = tokenize_and_pad(lines, 'english_sentence', max_length_src)
hin_tokenizer, hin_sequences = tokenize_and_pad(lines, 'hindi_sentence', max_length_tar)

In [27]:
num_encoder_tokens = len(eng_tokenizer.word_index) + 1
num_decoder_tokens = len(hin_tokenizer.word_index) + 1

In [28]:
print("English vocab size",num_encoder_tokens)
print("Hindi vocab size",num_decoder_tokens)

English vocab size 13985
Hindi vocab size 17471


In [29]:
X_train, X_test, y_train, y_test = train_test_split(eng_sequences, hin_sequences, test_size=0.2, random_state=42)

In [30]:
model = Sequential()
model.add(Embedding(num_encoder_tokens, 100, input_length=20, mask_zero=True))
model.add(LSTM(100))
model.add(RepeatVector(20))
model.add(LSTM(100, return_sequences=True))
model.add(Dense(num_decoder_tokens,activation='softmax'))

model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, 20, 100)           1398500   
                                                                 
 lstm (LSTM)                 (None, 100)               80400     
                                                                 
 repeat_vector (RepeatVecto  (None, 20, 100)           0         
 r)                                                              
                                                                 
 lstm_1 (LSTM)               (None, 20, 100)           80400     
                                                                 
 dense (Dense)               (None, 20, 17471)         1764571   
                                                                 
Total params: 3323871 (12.68 MB)
Trainable params: 3323871 (12.68 MB)
Non-trainable params: 0 (0.00 Byte)
________________

In [31]:
model.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])

model.fit(X_train, y_train, epochs=10, batch_size=32, validation_split=0.2)

Epoch 1/10
499/499 [==============================] - 36s 57ms/step - loss: 3.7848 - accuracy: 0.5786 - val_loss: 3.2516 - val_accuracy: 0.5783
Epoch 2/10
499/499 [==============================] - 17s 33ms/step - loss: 3.0696 - accuracy: 0.5892 - val_loss: 3.1190 - val_accuracy: 0.5888
Epoch 3/10
499/499 [==============================] - 16s 31ms/step - loss: 2.9957 - accuracy: 0.5928 - val_loss: 3.1162 - val_accuracy: 0.5909
Epoch 4/10
499/499 [==============================] - 15s 31ms/step - loss: 2.9526 - accuracy: 0.5938 - val_loss: 3.1231 - val_accuracy: 0.5909
Epoch 5/10
499/499 [==============================] - 16s 32ms/step - loss: 2.9198 - accuracy: 0.5947 - val_loss: 3.1433 - val_accuracy: 0.5888
Epoch 6/10
499/499 [==============================] - 15s 31ms/step - loss: 2.8943 - accuracy: 0.5950 - val_loss: 3.1616 - val_accuracy: 0.5889
Epoch 7/10
499/499 [==============================] - 15s 30ms/step - loss: 2.8707 - accuracy: 0.5952 - val_loss: 3.1797 - val_accuracy:

In [32]:
preds = model.predict(X_test[:100,:])
preds

4/4 [==============================] - 1s 7ms/step


array([[[3.55160492e-03, 6.57491270e-04, 1.74364701e-01, ...,
         4.59189124e-07, 9.48386347e-09, 8.01085154e-09],
        [4.01458517e-03, 6.69930875e-03, 9.24536865e-03, ...,
         1.71607167e-06, 2.46809773e-08, 2.19987015e-08],
        [7.41256680e-03, 2.19433382e-02, 7.84164481e-03, ...,
         3.15307807e-06, 4.00806748e-08, 3.67705546e-08],
        ...,
        [9.98762250e-01, 1.31895198e-04, 2.66630213e-05, ...,
         1.33635152e-11, 7.42614683e-13, 5.88311030e-13],
        [9.98763800e-01, 1.31727735e-04, 2.66787556e-05, ...,
         1.33407174e-11, 7.41055166e-13, 5.87085610e-13],
        [9.98764157e-01, 1.31642359e-04, 2.66918705e-05, ...,
         1.33258187e-11, 7.39946678e-13, 5.86215321e-13]],

       [[3.52562591e-03, 6.55735435e-04, 1.71195343e-01, ...,
         3.72893254e-07, 7.74857600e-09, 6.53483267e-09],
        [1.95378298e-03, 8.19436554e-03, 8.24923255e-03, ...,
         1.24773237e-06, 1.13193002e-08, 9.95210581e-09],
        [1.35016302e-03, 

In [33]:
predictions = np.argmax(preds, axis=1)

predictions

array([[19,  4,  0, ...,  2,  3,  3],
       [19,  8,  0, ...,  3,  5,  5],
       [19,  3,  0, ...,  0,  0,  0],
       ...,
       [19,  5,  0, ...,  2,  1,  1],
       [19,  7,  0, ...,  3,  5,  5],
       [19,  5,  0, ...,  2,  3,  3]])

In [34]:
def get_word(n,tokenizer):
    for word, index in tokenizer.word_index.items():
        if index == n:
            return word
    return None

In [ ]:
pred_text = []
for i in predictions:
    temp = []
    for j in range(len(i)):
        t = get_word(i[j], hin_tokenizer)
        if j > 0:
            if (t == get_word(i[j-1],hin_tokenizer)) or (t == None):
                temp.append('')
            else:
                temp.append(t)
        else:
            if (t==None):
                temp.append('')
            else:
                temp.append(t)
    print(temp)
    pred_text.append(' '.join(temp))

['पर', 'में', '', 'और', '', 'हैं', 'और', '', '', '', 'और', 'है', 'के', '', 'है', '', '', '', '', '', 'है', 'के', '', '', 'के', 'में', 'है', 'के', 'में', 'और', '', 'में', '', 'में', '', '', 'है', 'में', 'हैं', '', 'के', '', 'में', '', '', 'में', 'और', 'में', '', 'के', '', 'और', 'में', 'हैं', 'और', '', '', 'है', 'और', 'है', '', 'में', '', 'है', '', '', 'के', '', '', 'है', '', '', 'है', '', 'के', 'है', '', 'और', '', 'है', '', 'में', 'और', '', 'में', 'और', '', 'के', 'है', '', '', 'में', 'और', 'है', '', '', 'के', 'है', 'में', 'और', '', 'है', '', '', 'में', '', 'के', '', 'में', 'और', 'है', 'और', '', 'में', '', 'के', 'और', '', 'है', '', 'के', 'और', 'के', '', 'के', 'है', '', 'और', 'में', 'है', '', '', '', 'और', 'में', '', '', 'के', '', 'में', '', '', 'है', 'के', 'है', 'के', 'में', '', 'में', '', 'है', '', 'के', '', '', 'है', 'में', 'के', 'है', 'और', 'है', 'हैं', 'है', 'के', 'है', '', 'के', 'और', '', 'और', 'के', '', '', 'में', 'और', '', 'में', 'के', '', '', 'और', '', 'और', 'है', 'और', '', 'के',

In [36]:
pred_text[0]

'पर में  और  हैं और    और है के  है      है के   के में है के में और  में  में   है में हैं  के  में   में और में  के  और में हैं और   है और है  में  है   के   है   है  के है  और  है  में और  में और  के है   में और है   के है में और  है   में  के  में और है और  में  के और  है  के और के  के है  और में है    और में   के  में   है के है के में  में  है  के   है में के है और है हैं है के है  के और  और के   में और  में के   और  और है और  के  है के   में के  और के में है में और है के और   के में  और है और के में है  के में है  के  है के है के  है  और  के है में और के  के और है के  और  में है  और के और के  में और के में  और   के और के में  है  में और   में  है और  है में है के है  के में के और  है  के  है और के और  है और  है के और में   है के है और के और है के है और   के   और है और के  और के और   के है में   और के  और  है और है  है और  है   के  है और है  और है में और में  और में है और  और के है  और  के और में के में और   में के  और के और के और के  है  के  में के और के है के   और है में के में

In [39]:
for i in y_test[0]:
  t = get_word(i,hin_tokenizer)
  print(t)

इस
की
कोई
ज़रूरत
ही
नहीं
है
कि
None
None
None
None
None
None
None
None
None
None
None
None
